# Описание проекта

Допустим, мы работаем в добывающей компании «ГлавРосГосНефть». Нужно решить, где бурить новую скважину.

Нам предоставлены пробы нефти в трёх регионах: в каждом 10 000 месторождений, где измерили качество нефти и объём её запасов. Наша задача построить модель машинного обучения, которая поможет определить регион, где добыча принесёт наибольшую прибыль. Проанализируем возможную прибыль и риски техникой *Bootstrap.*

Шаги для выбора локации:

- В избранном регионе ищут месторождения, для каждого определяют значения признаков;
- Строят модель и оценивают объём запасов;
- Выбирают месторождения с самым высокими оценками значений. Количество месторождений зависит от бюджета компании и стоимости разработки одной скважины;
- Прибыль равна суммарной прибыли отобранных месторождений.

## Описание данных
Данные геологоразведки трёх регионов находятся в файлах:

`/datasets/geo_data_0.csv`,

`/datasets/geo_data_1.csv`,

`/datasets/geo_data_2.csv`.

id — уникальный идентификатор скважины;

f0, f1, f2 — три признака точек (неважно, что они означают, но сами признаки значимы);
product — объём запасов в скважине (тыс. баррелей).

## Содержание

1. [Загрузка и подготовка данных](#upload)<br>
2. [Обучение и проверка модели](#model)<br>
3. [Подготовка к расчету прибыли](#prep_profit)<br>
4. [Расчет прибыли и рисков](#calc_profit)

<a id='upload'> </a>
# 1. Загрузка и подготовка данных

In [1]:
import pandas as pd
import plotly.express as px
from sklearn.model_selection import train_test_split
from sklearn.linear_model import SGDRegressor
from sklearn.metrics import mean_squared_error as mse
import plotly.express as px
import numpy as np
from scipy import stats as st

In [2]:
geo_data_0 = pd.read_csv('/datasets/geo_data_0.csv')
geo_data_1 = pd.read_csv('/datasets/geo_data_1.csv')
geo_data_2 = pd.read_csv('/datasets/geo_data_2.csv')

Взглянем на наши данные и их размер

In [3]:
geo_data_0.head(10)

id        f0        f1        f2     product
0  txEyH  0.705745 -0.497823  1.221170  105.280062
1  2acmU  1.334711 -0.340164  4.365080   73.037750
2  409Wp  1.022732  0.151990  1.419926   85.265647
3  iJLyR -0.032172  0.139033  2.978566  168.620776
4  Xdl7t  1.988431  0.155413  4.751769  154.036647
5  wX4Hy  0.969570  0.489775 -0.735383   64.741541
6  tL6pL  0.645075  0.530656  1.780266   49.055285
7  BYPU6 -0.400648  0.808337 -5.624670   72.943292
8  j9Oui  0.643105 -0.551583  2.372141  113.356160
9  OLuZU  2.173381  0.563698  9.441852  127.910945

In [4]:
geo_data_1.head(10)

id         f0         f1        f2     product
0  kBEdx -15.001348  -8.276000 -0.005876    3.179103
1  62mP7  14.272088  -3.475083  0.999183   26.953261
2  vyE1P   6.263187  -5.948386  5.001160  134.766305
3  KcrkZ -13.081196 -11.506057  4.999415  137.945408
4  AHL4O  12.702195  -8.147433  5.004363  134.766305
5  HHckp  -3.327590  -2.205276  3.003647   84.038886
6  h5Ujo -11.142655 -10.133399  4.002382  110.992147
7  muH9x   4.234715  -0.001354  2.004588   53.906522
8  YiRkx  13.355129  -0.332068  4.998647  134.766305
9  jG6Gi   1.069227 -11.025667  4.997844  137.945408

In [5]:
geo_data_2.head(10)

id        f0        f1        f2     product
0  fwXo0 -1.146987  0.963328 -0.828965   27.758673
1  WJtFt  0.262778  0.269839 -2.530187   56.069697
2  ovLUW  0.194587  0.289035 -5.586433   62.871910
3  q6cA6  2.236060 -0.553760  0.930038  114.572842
4  WPMUX -0.515993  1.716266  5.899011  149.600746
5  LzZXx -0.758092  0.710691  2.585887   90.222465
6  WBHRv -0.574891  0.317727  1.773745   45.641478
7  XO8fn -1.906649 -2.458350 -0.177097   72.480640
8  ybmQ5  1.776292 -0.279356  3.004156  106.616832
9  OilcN -1.214452 -0.439314  5.922514   52.954532

In [6]:
geo_data_0.shape

(100000, 5)

In [7]:
geo_data_1.shape

(100000, 5)

In [8]:
geo_data_2.shape

(100000, 5)

Все 3 таблицы имеют одинаковый формат. Это очень хорошо для дальнейшей работы с ними

Изучим их на наличие пропущенных значений

In [9]:
def count_null_values(data):
    '''function takes 1 arg: dataframe and returns the amount of null values'''
    return data.isnull().sum().sum()

In [10]:
print('Количество пропущенных значений в первом регионе:', count_null_values(geo_data_0))
print('Количество пропущенных значений во втором регионе:', count_null_values(geo_data_1))
print('Количество пропущенных значений в третьем регионе:', count_null_values(geo_data_2))

Количество пропущенных значений в первом регионе: 0
Количество пропущенных значений во втором регионе: 0
Количество пропущенных значений в третьем регионе: 0


Видим, что пропущенных значений нет. Отлично. Теперь посмотрим, есть ли сильно выбивающиеся значения. Для этого построим `boxplot` и взглянем на каждый признак для каждого региона отдельно

In [11]:
def draw_boxplot(data):
    '''function draws 4 boxplots using f0, f1, f2 and product params'''
    params = ['f0', 'f1', 'f2', 'product']
    for param in params:
        fig = px.box(data, y=param, title='Распределение ' + param)
        fig.show()

Изучим для первого региона

In [12]:
draw_boxplot(geo_data_0)

Есть некоторые выбросы в распределении признака f2. Посмотрим, какую долю от общего набора данных составляют эти выбросы

In [13]:
UPPER_FENCE_0 = 11.4
LOWER_FENCE_0 = -6.4

In [14]:
def calc_part_outlayers(data, column, LOWER_FENCE, UPPER_FENCE):
    '''function calcs part of outlayers with required args:
    data, column, lower fence and upper fence'''
    return 1 - (((data[column] > LOWER_FENCE) & (data[column] < UPPER_FENCE)).sum()) / data.shape[0]

In [15]:
calc_part_outlayers(geo_data_0, column='f2', LOWER_FENCE=LOWER_FENCE_0, UPPER_FENCE=UPPER_FENCE_0)

0.0049200000000000355

Доля выбросов примерно 0.5%. Мы можем избавиться от выбросов, не потеряв при этом существенную часть данных. Это и сделаем

In [16]:
geo_data_0 = geo_data_0.query('f2 > @LOWER_FENCE_0 & f2 < @UPPER_FENCE_0')

Для второго региона

In [17]:
draw_boxplot(geo_data_1)

Видим выбросы у признака f1. Аналогично посмотрим какую долю они занимают

In [18]:
UPPER_FENCE_1 = 9.05
LOWER_FENCE_1 = -18.7

In [19]:
calc_part_outlayers(geo_data_1, column='f1', LOWER_FENCE=LOWER_FENCE_1, UPPER_FENCE=UPPER_FENCE_1)

0.006329999999999947

Доля выбросов менее 1%. Избавимся от них

In [20]:
geo_data_1 = geo_data_1.query('f1 > @LOWER_FENCE_1 & f1 < @UPPER_FENCE_1')

Для третьетго региона

In [21]:
draw_boxplot(geo_data_2)

У третьего региона мы видим, что выбросы есть по всем трём признакам. Изучим, какую долю они составляют суммарно

In [22]:
LOWER_FENCE_2_F0 = -4.64
UPPER_FENCE_2_F0 = 4.64

LOWER_FENCE_2_F1 = -4.68
UPPER_FENCE_2_F1 = 4.67

LOWER_FENCE_2_F2 = -6.95
UPPER_FENCE_2_F2 = 11.946

In [23]:
print(calc_part_outlayers(geo_data_2, column='f0', LOWER_FENCE=LOWER_FENCE_2_F0, UPPER_FENCE=UPPER_FENCE_2_F0))
print(calc_part_outlayers(geo_data_2, column='f1', LOWER_FENCE=LOWER_FENCE_2_F1, UPPER_FENCE=UPPER_FENCE_2_F1))
print(calc_part_outlayers(geo_data_2, column='f2', LOWER_FENCE=LOWER_FENCE_2_F2, UPPER_FENCE=UPPER_FENCE_2_F2))

0.007340000000000013
0.006859999999999977
0.005839999999999956


Видим, что суммарно все выбросы составляют ~1.5%, что не критично для избавления

In [24]:
geo_data_2 = geo_data_2.query('f0 > @LOWER_FENCE_2_F0 & f0 < @UPPER_FENCE_2_F0')
geo_data_2 = geo_data_2.query('f1 > @LOWER_FENCE_2_F1 & f1 < @UPPER_FENCE_2_F1')
geo_data_2 = geo_data_2.query('f2 > @LOWER_FENCE_2_F2 & f2 < @UPPER_FENCE_2_F2')

#### Удаление лишних столбцов

Столбец `id` для нашей модели не нужен, т.к. не представляет для неё никакой ценности. Удалим его

In [25]:
def drop_column(data):
    return data.drop('id', axis=1)

In [26]:
geo_data_0 = drop_column(geo_data_0)
geo_data_1 = drop_column(geo_data_1)
geo_data_2 = drop_column(geo_data_2)

#### Разбиение на train и valid

Напишем функцию, которая будет выделять целевые и таргетные переменные и делать разбиение на валидационную и тестовую выборки, чтобы нам осталость только вызвать её и присвоить результат работы нужным переменным

In [27]:
def train_valid_split(data):
    target = data['product']
    features = data.drop('product', axis=1)
    return train_test_split(features, target, test_size=0.25, random_state=10)

In [28]:
X_train_0, X_valid_0, Y_train_0, Y_valid_0 = train_valid_split(geo_data_0)
X_train_1, X_valid_1, Y_train_1, Y_valid_1 = train_valid_split(geo_data_1)
X_train_2, X_valid_2, Y_train_2, Y_valid_2 = train_valid_split(geo_data_2)

<a id='model'> </a>
# 2. Обучение и проверка модели

### Первый регион

Воспользуемся линейным регрессором `SGDRegressor`

In [29]:
model_0 = SGDRegressor()

Обучаем

In [30]:
model_0.fit(X_train_0, Y_train_0)

SGDRegressor(alpha=0.0001, average=False, early_stopping=False, epsilon=0.1,
             eta0=0.01, fit_intercept=True, l1_ratio=0.15,
             learning_rate='invscaling', loss='squared_loss', max_iter=1000,
             n_iter_no_change=5, penalty='l2', power_t=0.25, random_state=None,
             shuffle=True, tol=0.001, validation_fraction=0.1, verbose=0,
             warm_start=False)

Делаем предсказание

In [31]:
predictions_0 = model_0.predict(X_valid_0)

Считаем `rmse`

In [32]:
rmse_0 = (mse(Y_valid_0, predictions_0)) ** 0.5
print('RMSE для первого региона:', rmse_0)
print('Средний запас предсказанного сырья:', predictions_0.mean())

RMSE для первого региона: 37.71481637695064
Средний запас предсказанного сырья: 91.5610943194753


Ошибка получилась достаточно сильной. Посмотрим на распределение целевой переменной, чтобы в этом убедиться

In [33]:
fig = px.histogram(geo_data_0, x='product', title='Распределение целевой переменной')
fig.show()

### Второй регион

In [34]:
model_1 = SGDRegressor()

In [35]:
model_1.fit(X_train_1, Y_train_1)

SGDRegressor(alpha=0.0001, average=False, early_stopping=False, epsilon=0.1,
             eta0=0.01, fit_intercept=True, l1_ratio=0.15,
             learning_rate='invscaling', loss='squared_loss', max_iter=1000,
             n_iter_no_change=5, penalty='l2', power_t=0.25, random_state=None,
             shuffle=True, tol=0.001, validation_fraction=0.1, verbose=0,
             warm_start=False)

In [36]:
predictions_1 = model_1.predict(X_valid_1)

In [37]:
rmse_1 = (mse(Y_valid_1, predictions_1)) ** 0.5
print('RMSE для второго региона:', rmse_1)
print('Средний запас предсказанного сырья:', predictions_1.mean())

RMSE для второго региона: 0.9005915337761056
Средний запас предсказанного сырья: 68.57858806516624


Ошибка оказалась меньше 1 условной единицы. Это удивительно хорошее качество модели, что слишком подозрительно для простого алгоритма. Возможно, наша целевая переменная сильно коррелирует (и при том, линейно) с одним из признаков. Проверим это

In [38]:
geo_data_1.corr()

f0        f1        f2   product
f0       1.000000  0.178913 -0.001659 -0.030378
f1       0.178913  1.000000 -0.002813 -0.010234
f2      -0.001659 -0.002813  1.000000  0.999397
product -0.030378 -0.010234  0.999397  1.000000

Видим, что признак `f2` коррелирует с `product` очень и очень сильно. По сути, корреляция между ними 1, что и дало такое низкое rmse по итогу

### Третий регион

In [39]:
model_2 = SGDRegressor()

In [40]:
model_2.fit(X_train_2, Y_train_2)

SGDRegressor(alpha=0.0001, average=False, early_stopping=False, epsilon=0.1,
             eta0=0.01, fit_intercept=True, l1_ratio=0.15,
             learning_rate='invscaling', loss='squared_loss', max_iter=1000,
             n_iter_no_change=5, penalty='l2', power_t=0.25, random_state=None,
             shuffle=True, tol=0.001, validation_fraction=0.1, verbose=0,
             warm_start=False)

In [41]:
predictions_2 = model_2.predict(X_valid_2)

In [42]:
rmse_2 = (mse(Y_valid_2, predictions_2)) ** 0.5
print('RMSE для третьего региона:', rmse_2)
print('Средний запас предсказанного сырья:', predictions_2.mean())

RMSE для третьего региона: 40.40975738924892
Средний запас предсказанного сырья: 93.78498115931374


Здесь ошибка получилась примерно такая же, как и в первом регионе.

<a id='prep_profit'> </a>
# 3. Подготовка к расчёту прибыли

Введём необходимые переменные для дальнейшего расчета прибыли

In [43]:
BUDGET = 10000000000
PRICE_BARREL = 450
VOLUME = 1000
COUNT_WELL = 200

Расчитаем необходимый объем сырья, чтобы разработка была безубыточной

In [44]:
PRODUCT_AMOUNT = BUDGET / (PRICE_BARREL * VOLUME) # количество продукта, необходимое, чтобы иметь 0 прибыль
print('Количество единиц продукта для безубыточной разработки:', int(PRODUCT_AMOUNT))

Количество единиц продукта для безубыточной разработки: 22222


Сравним это количество со средним запасом в каждом регионе

In [45]:
def compare_with_mean(data, product_amount, count_well):
    '''data - dataset
    product_amount - budget / profit (the amount of product in order to have 0 profit)
    halls - the amount of halls (default 200)'''
    
    product = data['product'].mean() * COUNT_WELL
    difference = product - PRODUCT_AMOUNT
    
    if difference < 0:
        return 'Для безубыточной разработки в регионе не хватает:', difference * (-1), 'единиц продукта'
    
    return 'Количество единиц продукта, которое приносит прибыль:', difference

Для первого региона

In [46]:
compare_with_mean(geo_data_0, product_amount=PRODUCT_AMOUNT, count_well=COUNT_WELL)

('Для безубыточной разработки в регионе не хватает:',
 3722.336565661255,
 'единиц продукта')

Для второго региона

In [47]:
compare_with_mean(geo_data_1, product_amount=PRODUCT_AMOUNT, count_well=COUNT_WELL)

('Для безубыточной разработки в регионе не хватает:',
 8460.315698617049,
 'единиц продукта')

Для третьего региона

In [48]:
compare_with_mean(geo_data_2, product_amount=PRODUCT_AMOUNT, count_well=COUNT_WELL)

('Для безубыточной разработки в регионе не хватает:',
 3265.133418972324,
 'единиц продукта')

Видим, что если брать средние значения, то в каждом регионе разработка будет убыточной

<a id='calc_profit'> </a>
# 4. Расчёт прибыли и рисков 

Воспользуемся технологией `bootstrap` для расчета прибыли и рисков

In [49]:
predictions_0 = pd.Series(predictions_0)
predictions_1 = pd.Series(predictions_1)
predictions_2 = pd.Series(predictions_2)

In [74]:
# добавление расчета рисков в bootstrap
def profit(target, pred):
    wells_sorted = pred.sort_values(ascending=False)
    top200_wells = target.loc[wells_sorted.index.to_list()][:200]
    return top200_wells.sum() * PRICE_BARREL * VOLUME - BUDGET
 
# Применяем технику бутстрап для подсчета средней  прибыли

state = np.random.RandomState(12345)
def bootstrap(target_valid, predictions, region, count_samples=1000):
 
    """Из  valid выборки функция генерирует 1000 подвыборок размера 500. При помощи вызова функции profit
    считается истинная прибыль"""
    values = []
    target_0 = Y_valid_0.reset_index(drop=True)
    target_1 = Y_valid_1.reset_index(drop=True)
    target_2 = Y_valid_2.reset_index(drop=True)
    
    if region == 0:
        target = target_0
    elif region == 1:
        target = target_1
    elif region == 2:
        target = target_2
    
    loss = 0 # убыточные случаи [+]
    for i in range(count_samples):
 
        target_sub = target.sample(n=500, replace=True, random_state=state)
        pred_sub = predictions.loc[target_sub.index.to_list()]
        value = profit(target_sub, pred_sub)
        values.append(value)
        
        if float(value) < 0: 
            loss += 1 
        
    loss_part = loss / count_samples
 
    values = pd.Series(values)
    
    lower = values.quantile(0.025) # fix №3
    upper = values.quantile(0.975) # fix №3
 
    return lower, upper, values, loss_part

Применим теперь функцию расчета прибыли и рисков к 3 регионам

In [52]:
Y_valid_0 = pd.Series(Y_valid_0)
lower_0, upper_0, res_0, loss_part_0 = bootstrap(Y_valid_0, predictions_0, region=0)

In [53]:
Y_valid_1 = pd.Series(Y_valid_1)
lower_1, upper_1, res_1, loss_part_1 = bootstrap(Y_valid_1, predictions_1, region=1)

In [54]:
Y_valid_2 = pd.Series(Y_valid_2)
lower_2, upper_2, res_2, loss_part_2 = bootstrap(Y_valid_2, predictions_2, region=2)

In [67]:
print('Прибыль в первом регионе:', res_0.sum(), ', риск убытков при этом:', round(loss_part_0, 2) * 100,'%')
print('Прибыль во втором регионе:',res_1.sum(), ', риск убытков при этом:', round(loss_part_1, 2) * 100,'%')
print('Прибыль в третьем регионе:',res_2.sum(), ', риск убытков при этом:', round(loss_part_2, 2) * 100,'%')

Прибыль в первом регионе: 439560935393.4709 , риск убытков при этом: 6.0 %
Прибыль во втором регионе: 471944689336.222 , риск убытков при этом: 1.0 %
Прибыль в третьем регионе: 278944047357.9447 , риск убытков при этом: 15.0 %


При этом доверительный интервал для регионов находится

In [83]:
print('Для первого региона в промежутке от', lower_0, 'до', upper_0)
print('Для второго региона в промежутке от ', lower_1, 'до', upper_1)
print('Для третьего региона в промежутке от ', lower_2, 'до', upper_2)

Для первого региона в промежутке от -104953460.00205702 до 989834089.6492822
Для второго региона в промежутке от  69521658.63108687 до 872219835.4030304
Для третьего региона в промежутке от  -281649875.77137977 до 802712279.3934906


### Выбор региона

Итак, лучше всего для разработки выбрать **второй** регион. И на это есть две причины.
- 1. Прибыль в этом регионе максимальная
- 2. Наша модель показала наилучшую точность, которая ощутимо лучше, чем в других регионах. Это говорит о минимальных рисках и максимально реалистичному расчету прибыли